<a href="https://colab.research.google.com/github/jalkestrup/dtu-deep-project/blob/main/llm2vec_scandeval_colab.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## Setting up colab env

In [2]:
! pip install -q seb
! pip install -q llm2vec
! pip install -q -U "huggingface_hub[cli]"

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 83.7/83.7 kB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.0/44.0 kB 3.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 53.6/53.6 kB 4.6 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 702.3/702.3 kB 21.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 119.2/119.2 kB 6.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 542.1/542.1 kB 25.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 6.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 172.0/172.0 kB 9.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 219.2/219.2 kB 11.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 6.1 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 11.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━

In [1]:
! huggingface-cli login


    _|    _|  _|    _|    _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|_|_|_|    _|_|      _|_|_|  _|_|_|_|
    _|    _|  _|    _|  _|        _|          _|    _|_|    _|  _|            _|        _|    _|  _|        _|
    _|_|_|_|  _|    _|  _|  _|_|  _|  _|_|    _|    _|  _|  _|  _|  _|_|      _|_|_|    _|_|_|_|  _|        _|_|_|
    _|    _|  _|    _|  _|    _|  _|    _|    _|    _|    _|_|  _|    _|      _|        _|    _|  _|        _|
    _|    _|    _|_|      _|_|_|    _|_|_|  _|_|_|  _|      _|    _|_|_|      _|        _|    _|    _|_|_|  _|_|_|_|

    A token is already saved on your machine. Run `huggingface-cli whoami` to get more information or `huggingface-cli logout` if you want to log out.
    Setting a new token will erase the existing one.
    To log in, `huggingface_hub` requires a token generated from https://huggingface.co/settings/tokens .
Enter your token (input will not be visible): Traceback (most recent call last):
  File "/home/lenovo/alkestrup/venv/

## Loading LLM model

In [23]:
from llm2vec import LLM2Vec

import torch
from transformers import AutoTokenizer, AutoModel, AutoConfig
from peft import PeftModel

# Loading base Mistral model, along with custom code that enables bidirectional connections in decoder-only LLMs. MNTP LoRA weights are merged into the base model.
tokenizer = AutoTokenizer.from_pretrained(
    "McGill-NLP/LLM2Vec-Sheared-LLaMA-mntp"
)
config = AutoConfig.from_pretrained(
    "McGill-NLP/LLM2Vec-Sheared-LLaMA-mntp", trust_remote_code=True
)
model = AutoModel.from_pretrained(
    "McGill-NLP/LLM2Vec-Sheared-LLaMA-mntp",
    trust_remote_code=True,
    config=config,
    torch_dtype=torch.bfloat16,
    device_map="cuda" if torch.cuda.is_available() else "cpu",
)
model = PeftModel.from_pretrained(
    model,
    "McGill-NLP/LLM2Vec-Sheared-LLaMA-mntp",
)
model = model.merge_and_unload()  # This can take several minutes on cpu

# Loading supervised model. This loads the trained LoRA weights on top of MNTP model. Hence the final weights are -- Base model + MNTP (LoRA) + supervised (LoRA).
model = PeftModel.from_pretrained(
    model, "McGill-NLP/LLM2Vec-Sheared-LLaMA-mntp-supervised"
)

# Wrapper for encoding and pooling operations
l2v = LLM2Vec(model, tokenizer, pooling_mode="mean", max_length=512)


Some weights of the model checkpoint at princeton-nlp/Sheared-LLaMA-1.3B were not used when initializing LlamaEncoderModel: ['lm_head.weight']
- This IS expected if you are initializing LlamaEncoderModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing LlamaEncoderModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


## Set up model in SEB and run eval
Intanstiate a custom model in the scandinavian embedding benchmark

~ Took +2 hrs to run 70% of eval when I interuped

In [ ]:
from sentence_transformers import SentenceTransformer
from typing import Any
import seb
import numpy as np


model_name = "LLM2Vec-Sheared-LLaMA-mntp-supervised"


class MyEncoder(seb.Encoder):
    """
    A custom model for SEB that uses the SentenceTransformer library.
    """

    def __init__(self, l2v):
        self.model = l2v

    def encode(  # type: ignore
        self,
        sentences: list[str],
        *,
        task: seb.Task,
        **kwargs: Any,
    ) -> np.ndarray:
        if task.name == "DKHate":  # allow you to embed differently based on the task
            emb = self.model.encode(sentences, batch_size=32)
        else:
            emb = self.model.encode(sentences, batch_size=32)  # here we just do the same for all tasks
        return emb


@seb.models.register(model_name)  # add the model to the registry
def create_my_model() -> seb.SebModel:
    hf_name = model_name

    # create meta data
    meta = seb.ModelMeta(
        name=hf_name.split("/")[-1],
        huggingface_name=hf_name,
        reference="https://huggingface.co/McGill-NLP/LLM2Vec-Sheared-LLaMA-mntp-supervised",
        languages=[],
        embedding_size=4096,
    )
    return seb.SebModel(
        encoder=MyEncoder(l2v),
        meta=meta,
    )

In [ ]:
task = seb.get_task("DKHate")

full_benchmark = seb.Benchmark(languages=['da'], tasks=[task])
results = full_benchmark.evaluate_models(models=models)

## Custom instructions

In [1]:
from llm2vec import LLM2Vec

import torch
from transformers import AutoTokenizer, AutoModel, AutoConfig
from peft import PeftModel

# Loading base Mistral model, along with custom code that enables bidirectional connections in decoder-only LLMs. MNTP LoRA weights are merged into the base model.
tokenizer = AutoTokenizer.from_pretrained(
    "jealk/llm2vec-da-mntp"
)
config = AutoConfig.from_pretrained(
    "jealk/llm2vec-da-mntp", trust_remote_code=True
)
model = AutoModel.from_pretrained(
    "jealk/llm2vec-da-mntp",
    trust_remote_code=True,
    config=config,
    torch_dtype=torch.bfloat16,
    device_map="cuda" if torch.cuda.is_available() else "cpu",
)
model = PeftModel.from_pretrained(
    model,
    "jealk/llm2vec-da-mntp",
)
model = model.merge_and_unload()  # This can take several minutes on cpu

# Loading supervised model. This loads the trained LoRA weights on top of MNTP model. Hence the final weights are -- Base model + MNTP (LoRA) + supervised (LoRA).
model = PeftModel.from_pretrained(
    model, "jealk/llm2vec-da-simcse"
)

# Wrapper for encoding and pooling operations
l2v = LLM2Vec(model, tokenizer, pooling_mode="mean", max_length=512)

/home/lenovo/alkestrup/venv/lib/python3.10/site-packages/huggingface_hub/file_download.py:797: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(
Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.


Loading checkpoint shards:   0%|          | 0/4 [00:00<?, ?it/s]

Some weights of the model checkpoint at AI-Sweden-Models/Llama-3-8B-instruct were not used when initializing LlamaEncoderModel: ['lm_head.weight']
- This IS expected if you are initializing LlamaEncoderModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing LlamaEncoderModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


In [7]:
l2v.encode([['embed to retrieve stuff','SomeTest sentence, continue writing about cows']])

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

tensor([[-1.9297, -1.3516,  4.3750,  ..., -4.5938,  0.3965,  1.3203]])

In [29]:
from typing import Any
import seb
from seb.interfaces.task import Task
import numpy as np
from tqdm import tqdm
from typing import Any, Optional, TypeVar
from collections.abc import Iterable, Sequence
from transformers import AutoTokenizer, BatchEncoding
from itertools import islice

T = TypeVar("T")
model_name = "LLM2Vec-Sheared-LLaMA-mntp-supervised"

def task_to_instruction(task: Task) -> str:
    if task.task_type in ["STS"]:
        return "Retrieve semantically similar text"
    if task.task_type in ["Summarization"]:
        return "Given a news summary, retrieve other semantically similar summaries"
    if task.task_type in ["BitextMining"]:
        task_name_to_instruct: dict[str, str] = {
            "Bornholm Parallel": "Retrieve parallel sentences in Danish and Bornholmsk",
            "Norwegian courts": "Retrieve parallel sentences in Norwegian Bokmål and Nynorsk",
        }
        default_instruction = "Retrieve parallel sentences."
        return task_name_to_instruct.get(task.name, default_instruction)
    if task.task_type in ["Classification"]:
        task_name_to_instruct: dict[str, str] = {
            "Angry Tweets": "Classify Danish tweets by sentiment. (positive, negative, neutral)",
            "DKHate": "Classify Danish tweets based on offensiveness (offensive, not offensive)",
            "Da Political Comments": "Classify Danish political comments for sentiment",
            "DaLAJ": "Classify texts based on linguistic acceptability in Swedish",
            "LCC": "Classify texts based on sentiment",
            "Language Identification": "Classify texts based on language",
            "Massive Intent": "Given a user utterance as query, find the user intents",
            "Massive Scenario": "Given a user utterance as query, find the user scenarios",
            "NoReC": "Classify Norwegian reviews by sentiment",
            "SweReC": "Classify Swedish reviews by sentiment",
            "Norwegian parliament": "Classify parliament speeches in Norwegian based on political affiliation",
            "ScaLA": "Classify passages in Scandinavian Languages based on linguistic acceptability",
        }
        default_instruction = "Classify user passages"
        return task_name_to_instruct.get(task.name, default_instruction)
    if task.task_type in ["Clustering"]:
        task_name_to_instruct: dict[str, str] = {
            "ArxivClusteringP2P": "Identify the main and secondary category of Arxiv papers based on the titles and abstracts",
            "VG Clustering": "Identify the categories (e.g. sports) of given articles in Norwegian",
            "SNL Clustering": "Identify categories in a Norwegian lexicon",
            "SwednClustering": "Identify news categories in Swedish passages",
        }
        default_instruction = "Identify categories in user passages"
        return task_name_to_instruct.get(task.name, default_instruction)
    if task.task_type in ["Reranking"]:
        return "Retrieve semantically similar passages."
    if task.task_type in ["Retrieval"]:
        task_name_to_instruct: dict[str, str] = {
            "Twitterhjerne": "Retrieve answers to questions asked in Danish tweets",
            "SwednRetrieval": "Given a Swedish news headline retrieve summaries or news articles",
            "TV2Nord Retrieval": "Given a summary of a Danish news article retrieve the corresponding news article",
            "DanFEVER": "Given a claim in Danish, retrieve documents that support the claim",
            "SNL Retrieval": "Given a lexicon headline in Norwegian, retrieve its article",
            "NorQuad": "Given a question in Norwegian, retrieve the answer from Wikipedia articles",
            "SweFAQ": "Retrieve answers given questions in Swedish",
            "ArguAna": "Given a claim, find documents that refute the claim",
            "ClimateFEVER": "Given a claim about climate change, retrieve documents that support or refute the claim",
        }
        default_instruction = "Retrieve text based on user query."
        return task_name_to_instruct.get(task.name, default_instruction)
    return ""

def batched(iterable: Iterable[T], n: int) -> Iterable[tuple[T, ...]]:
    # batched('ABCDEFG', 3) --> ABC DEF G
    if n < 1:
        raise ValueError("n must be at least one")
    it = iter(iterable)
    while batch := tuple(islice(it, n)):
        yield batch


class SEB_L2V(seb.Encoder):
    """
    A custom model for SEB that uses the SentenceTransformer library.
    """

    def __init__(self, model_name: str, max_length: int, max_batch_size: Optional[int] = None, **kwargs: Any):
        self.model = l2v
        self.tokenizer = AutoTokenizer.from_pretrained("jealk/llm2vec-da-mntp")
        self.max_length = max_length
        self.max_batch_size = max_batch_size
        
    def preprocess(self, sentences: Sequence[str], instruction: str) -> BatchEncoding:
        if instruction is not None:
            sentences = [[instruction,sentence] for sentence in sentences]
        else:
            sentences = [sentence for sentence in sentences]

        #batch_dict = self.tokenizer(
        #    sentences,  # type: ignore
        #    max_length=512,
        #    padding=True,
        #    truncation=True,
        #    return_tensors="pt",
        #)

        return sentences
    
    def encode(  # type: ignore
        self,
        sentences: list[str],
        *,
        task: seb.Task,
        batch_size: int = 128,
        **kwargs: Any,
    ) -> np.ndarray:
        
        if self.max_batch_size and batch_size > self.max_batch_size:
            batch_size = self.max_batch_size
        batched_embeddings = []
        if task is not None:  # noqa
            instruction = task_to_instruction(task)
        else:
            instruction = None
        for batch in tqdm(batched(sentences, batch_size)): 
            # Preprocess the batch in the required format
            preprocessed_batch = self.preprocess(batch, instruction=instruction)
            with torch.inference_mode():
                embedded_batch = self.model.encode(preprocessed_batch)
            # Since no post-processing is needed, just append the embeddings
            batched_embeddings.append(embedded_batch)
        # Concatenate the batches along the first dimension (i.e., the batch dimension)

        return torch.cat(batched_embeddings).numpy() 


model_name = "llm2vec-da-simcse"
@seb.models.register(model_name)  # add the model to the registry
def create_my_model() -> seb.SebModel:
    hf_name = model_name

    # create meta data
    meta = seb.ModelMeta(
        name=hf_name.split("/")[-1],
        huggingface_name=hf_name,
        reference="https://huggingface.co/jealk/{model_name}",
        languages=[],
        embedding_size=4096,
    )
    return seb.SebModel(
        encoder=SEB_L2V(l2v, max_length=256, max_batch_size=128),
        meta=meta,
    )

In [31]:
import seb

models = [seb.get_model("llm2vec-da-simcse")]
# for simplicity, we will only run it with one model, but you could run it with multiple models:
# models = seb.get_all_models()
task = seb.get_task("DKHate")

full_benchmark = seb.Benchmark(languages=['da'])
results = full_benchmark.evaluate_models(models=models)

Special tokens have been added in the vocabulary, make sure the associated word embeddings are fine-tuned or trained.
Running llm2vec-da-simcse:   0%|          | 0/1 [00:00<?, ?it/s]

Generating train split: 0 examples [00:00, ? examples/s]

Generating test split: 0 examples [00:00, ? examples/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

...

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]


6it [00:02,  2.55it/s]
Running llm2vec-da-simcse: 100%|██████████| 1/1 [15:19<00:00, 919.22s/it]


In [32]:
results[0].task_results

[TaskResult(task_name='Angry Tweets', task_description='A sentiment dataset with 3 classes (positiv, negativ, neutral) for Danish tweets', task_version='1.1.1', time_of_run=datetime.datetime(2024, 11, 19, 19, 4, 51, 259680), scores={'da': {'accuracy': 0.5544412607449857, 'f1': 0.5474864912529586, 'accuracy_stderr': 0.022839909620869108, 'f1_stderr': 0.020423362260178386, 'main_score': 0.5544412607449857}}, main_score='accuracy'),
 TaskResult(task_name='LCC', task_description='The leipzig corpora collection, annotated for sentiment', task_version='1.1.1', time_of_run=datetime.datetime(2024, 11, 19, 19, 5, 8, 613348), scores={'da': {'accuracy': 0.5846666666666668, 'f1': 0.5700252795868102, 'accuracy_stderr': 0.05609911863043047, 'f1_stderr': 0.0536466175397885, 'main_score': 0.5846666666666668}}, main_score='accuracy'),
 TaskResult(task_name='Bornholm Parallel', task_description='Danish Bornholmsk Parallel Corpus. Bornholmsk is a Danish dialect spoken on the island of Bornholm, Denmark. 

In [34]:
results[0].average_score

AttributeError: 'BenchmarkResults' object has no attribute 'average_score'